In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option("display.max_columns", None)
pd.set_option("display.max_rows", None)

import json # library to handle JSON files

from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from bs4 import BeautifulSoup # library to parse HTML and XML documents

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

import folium # map rendering library

print("Libraries imported.")

Libraries imported.


In [2]:
data = requests.get('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M').text
soup = BeautifulSoup(data, 'html.parser')
# create three lists to store table data
postalCodeList = []
boroughList = []
neighborhoodList = []

In [3]:
# append the data into the respective lists
for row in soup.find('table').find_all('tr'):
    cells = row.find_all('td')
    if(len(cells) > 0):
        postalCodeList.append(cells[0].text)
        boroughList.append(cells[1].text)
        neighborhoodList.append(cells[2].text) # avoid new lines in neighborhood cell

In [4]:
# create a new DataFrame from the three lists
toronto_df = pd.DataFrame({"PostalCode": postalCodeList,
                           "Borough": boroughList,
                           "Neighborhood": neighborhoodList})

toronto_df.head()

PostalCode             Borough                 Neighborhood
0      M1A\n      Not assigned\n               Not assigned\n
1      M2A\n      Not assigned\n               Not assigned\n
2      M3A\n        North York\n                  Parkwoods\n
3      M4A\n        North York\n           Victoria Village\n
4      M5A\n  Downtown Toronto\n  Regent Park, Harbourfront\n

In [5]:
# drop cells with a borough that is Not assigned
toronto_df_dropna = toronto_df[toronto_df.Borough != "Not assigned\n"].reset_index(drop=True)
toronto_df_dropna.head()

PostalCode             Borough  \
0      M3A\n        North York\n   
1      M4A\n        North York\n   
2      M5A\n  Downtown Toronto\n   
3      M6A\n        North York\n   
4      M7A\n  Downtown Toronto\n   

                                    Neighborhood  
0                                    Parkwoods\n  
1                             Victoria Village\n  
2                    Regent Park, Harbourfront\n  
3             Lawrence Manor, Lawrence Heights\n  
4  Queen's Park, Ontario Provincial Government\n

In [6]:
toronto_df_dropna["PostalCode"] = toronto_df_dropna["PostalCode"].str.replace("\n","")
toronto_df_dropna.head()

PostalCode             Borough  \
0        M3A        North York\n   
1        M4A        North York\n   
2        M5A  Downtown Toronto\n   
3        M6A        North York\n   
4        M7A  Downtown Toronto\n   

                                    Neighborhood  
0                                    Parkwoods\n  
1                             Victoria Village\n  
2                    Regent Park, Harbourfront\n  
3             Lawrence Manor, Lawrence Heights\n  
4  Queen's Park, Ontario Provincial Government\n

In [7]:
toronto_df_dropna["Borough"] = toronto_df_dropna["Borough"].str.replace("\n","")
toronto_df_dropna.head()

PostalCode           Borough                                   Neighborhood
0        M3A        North York                                    Parkwoods\n
1        M4A        North York                             Victoria Village\n
2        M5A  Downtown Toronto                    Regent Park, Harbourfront\n
3        M6A        North York             Lawrence Manor, Lawrence Heights\n
4        M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government\n

In [8]:
toronto_df_dropna["Neighborhood"] = toronto_df_dropna["Neighborhood"].str.replace("\n","")
toronto_df_dropna.head()

PostalCode           Borough                                 Neighborhood
0        M3A        North York                                    Parkwoods
1        M4A        North York                             Victoria Village
2        M5A  Downtown Toronto                    Regent Park, Harbourfront
3        M6A        North York             Lawrence Manor, Lawrence Heights
4        M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

In [9]:
# group neighborhoods in the same borough
toronto_df_grouped = toronto_df_dropna.groupby(["PostalCode", "Borough"], as_index=False).agg(lambda x: ", ".join(x))
toronto_df_grouped.head()

PostalCode      Borough                            Neighborhood
0        M1B  Scarborough                          Malvern, Rouge
1        M1C  Scarborough  Rouge Hill, Port Union, Highland Creek
2        M1E  Scarborough       Guildwood, Morningside, West Hill
3        M1G  Scarborough                                  Woburn
4        M1H  Scarborough                               Cedarbrae

In [10]:
# for Neighborhood="Not assigned", make the value the same as Borough
for index, row in toronto_df_grouped.iterrows():
    if row["Neighborhood"] == "Not assigned":
        row["Neighborhood"] = row["Borough"]
        
toronto_df_grouped.head()

PostalCode      Borough                            Neighborhood
0        M1B  Scarborough                          Malvern, Rouge
1        M1C  Scarborough  Rouge Hill, Port Union, Highland Creek
2        M1E  Scarborough       Guildwood, Morningside, West Hill
3        M1G  Scarborough                                  Woburn
4        M1H  Scarborough                               Cedarbrae

In [11]:
toronto_df_grouped.shape

(103, 3)

In [12]:
# load the coordinates from the csv file on Coursera
coordinates = pd.read_csv("Geospatial_Coordinates.csv")
coordinates.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [13]:
coordinates.rename(columns={"Postal Code": "PostalCode"}, inplace=True)
coordinates.head()

PostalCode   Latitude  Longitude
0        M1B  43.806686 -79.194353
1        M1C  43.784535 -79.160497
2        M1E  43.763573 -79.188711
3        M1G  43.770992 -79.216917
4        M1H  43.773136 -79.239476

In [14]:
# merge two table on the column "PostalCode"
toronto_df1 = toronto_df_grouped.merge(coordinates, on="PostalCode", how="left")
toronto_df1.head()

PostalCode      Borough                            Neighborhood   Latitude  \
0        M1B  Scarborough                          Malvern, Rouge  43.806686   
1        M1C  Scarborough  Rouge Hill, Port Union, Highland Creek  43.784535   
2        M1E  Scarborough       Guildwood, Morningside, West Hill  43.763573   
3        M1G  Scarborough                                  Woburn  43.770992   
4        M1H  Scarborough                               Cedarbrae  43.773136   

   Longitude  
0 -79.194353  
1 -79.160497  
2 -79.188711  
3 -79.216917  
4 -79.239476

In [15]:
# create a new test dataframe
column_names = ["PostalCode", "Borough", "Neighborhood", "Latitude", "Longitude"]
test_df = pd.DataFrame(columns=column_names)

test_list = ["M5G", "M2H", "M4B", "M1J", "M4G", "M4M", "M1R", "M9V", "M9L", "M5V", "M1B", "M5A"]

for postcode in test_list:
    test_df = test_df.append(toronto_df1[toronto_df1["PostalCode"]==postcode], ignore_index=True)
    
test_df

PostalCode           Borough  \
0         M5G  Downtown Toronto   
1         M2H        North York   
2         M4B         East York   
3         M1J       Scarborough   
4         M4G         East York   
5         M4M      East Toronto   
6         M1R       Scarborough   
7         M9V         Etobicoke   
8         M9L        North York   
9         M5V  Downtown Toronto   
10        M1B       Scarborough   
11        M5A  Downtown Toronto   

                                         Neighborhood   Latitude  Longitude  
0                                  Central Bay Street  43.657952 -79.387383  
1                                   Hillcrest Village  43.803762 -79.363452  
2                     Parkview Hill, Woodbine Gardens  43.706397 -79.309937  
3                                 Scarborough Village  43.744734 -79.239476  
4                                             Leaside  43.709060 -79.363452  
5                                     Studio District  43.659526 -79.340923  
6                                   Wexford, Maryvale  43.750072 -79.295849  
7   South Steeles, Silverstone, Humbergate, Jamest...  43.739416 -79.588437  
8                                       Humber Summit  43.756303 -79.565963  
9   CN Tower, King and Spadina, Railway Lands, Har...  43.628947 -79.394420  
10                                     Malvern, Rouge  43.806686 -79.194353  
11                          Regent Park, Harbourfront  43.654260 -79.360636

In [16]:
toronto_df_new = toronto_df1.dropna(axis=0)
toronto_df_new.head()

PostalCode      Borough                            Neighborhood   Latitude  \
0        M1B  Scarborough                          Malvern, Rouge  43.806686   
1        M1C  Scarborough  Rouge Hill, Port Union, Highland Creek  43.784535   
2        M1E  Scarborough       Guildwood, Morningside, West Hill  43.763573   
3        M1G  Scarborough                                  Woburn  43.770992   
4        M1H  Scarborough                               Cedarbrae  43.773136   

   Longitude  
0 -79.194353  
1 -79.160497  
2 -79.188711  
3 -79.216917  
4 -79.239476

In [18]:
toronto_df_new.groupby('Borough').count()['Neighborhood']

Borough
Central Toronto      9
Downtown Toronto    19
East Toronto         5
East York            5
Etobicoke           12
Mississauga          1
North York          24
Scarborough         17
West Toronto         6
York                 5
Name: Neighborhood, dtype: int64

In [17]:
address = 'Toronto'

geolocator = Nominatim(user_agent="my-application")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.6534817, -79.3839347.


In [19]:
# create map of Toronto using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(toronto_df_new['Latitude'], toronto_df_new['Longitude'], toronto_df_new['Borough'], toronto_df_new['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_toronto)  
    
map_toronto

In [20]:
# filter borough names that contain the word Toronto
borough_names = list(toronto_df_new.Borough.unique())

borough_with_toronto = []

for x in borough_names:
    if "toronto" in x.lower():
        borough_with_toronto.append(x)
        
borough_with_toronto

['East Toronto', 'Central Toronto', 'Downtown Toronto', 'West Toronto']

In [21]:
# create a new DataFrame with only boroughs that contain the word Toronto
toronto_df_new = toronto_df_new[toronto_df_new['Borough'].isin(borough_with_toronto)].reset_index(drop=True)
print(toronto_df_new.shape)
toronto_df_new.head()

(39, 5)


PostalCode          Borough                    Neighborhood   Latitude  \
0        M4E     East Toronto                     The Beaches  43.676357   
1        M4K     East Toronto    The Danforth West, Riverdale  43.679557   
2        M4L     East Toronto  India Bazaar, The Beaches West  43.668999   
3        M4M     East Toronto                 Studio District  43.659526   
4        M4N  Central Toronto                   Lawrence Park  43.728020   

   Longitude  
0 -79.293031  
1 -79.352188  
2 -79.315572  
3 -79.340923  
4 -79.388790

In [22]:
# create map of Toronto using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(toronto_df_new['Latitude'], toronto_df_new['Longitude'], toronto_df_new['Borough'], toronto_df_new['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_toronto)  
    
map_toronto

In [29]:
# define Foursquare Credentials and Version
CLIENT_ID = 'AROKBSC2ITZXX3VJINCAVEP5UWGV3U30P534PETOIQFHXB33' # your Foursquare ID
CLIENT_SECRET = 'JMFT4CUCXIGG5PJMY41ZJANODXY2RXOXVD3OGKQCGJDBHB5Z' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: AROKBSC2ITZXX3VJINCAVEP5UWGV3U30P534PETOIQFHXB33
CLIENT_SECRET:JMFT4CUCXIGG5PJMY41ZJANODXY2RXOXVD3OGKQCGJDBHB5Z


In [123]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [125]:

#Get venues for all neighborhoods in our dataset
toronto_venues = getNearbyVenues(names=toronto_df_new['Neighborhood'],
                                latitudes=toronto_df_new['Latitude'],
                                longitudes=toronto_df_new['Longitude'])

The Beaches
The Danforth West, Riverdale
India Bazaar, The Beaches West
Studio District
Lawrence Park
Davisville North
North Toronto West,  Lawrence Park
Davisville
Moore Park, Summerhill East
Summerhill West, Rathnelly, South Hill, Forest Hill SE, Deer Park
Rosedale
St. James Town, Cabbagetown
Church and Wellesley
Regent Park, Harbourfront
Garden District, Ryerson
St. James Town
Berczy Park
Central Bay Street
Richmond, Adelaide, King
Harbourfront East, Union Station, Toronto Islands
Toronto Dominion Centre, Design Exchange
Commerce Court, Victoria Hotel
Roselawn
Forest Hill North & West, Forest Hill Road Park
The Annex, North Midtown, Yorkville
University of Toronto, Harbord
Kensington Market, Chinatown, Grange Park
CN Tower, King and Spadina, Railway Lands, Harbourfront West, Bathurst Quay, South Niagara, Island airport
Stn A PO Boxes
First Canadian Place, Underground city
Christie
Dufferin, Dovercourt Village
Little Portugal, Trinity
Brockton, Parkdale Village, Exhibition Place
High

In [126]:

#Check size of resulting dataframe
toronto_venues.shape

(1623, 7)

In [127]:
toronto_venues.head()

Neighborhood  Neighborhood Latitude  \
0                   The Beaches              43.676357   
1                   The Beaches              43.676357   
2                   The Beaches              43.676357   
3                   The Beaches              43.676357   
4  The Danforth West, Riverdale              43.679557   

   Neighborhood Longitude                               Venue  Venue Latitude  \
0              -79.293031                   Glen Manor Ravine       43.676821   
1              -79.293031  The Big Carrot Natural Food Market       43.678879   
2              -79.293031                 Grover Pub and Grub       43.679181   
3              -79.293031                       Upper Beaches       43.680563   
4              -79.352188                       MenEssentials       43.677820   

   Venue Longitude     Venue Category  
0       -79.293942              Trail  
1       -79.297734  Health Food Store  
2       -79.297215                Pub  
3       -79.292869       Neighborhood  
4       -79.351265     Cosmetics Shop

In [128]:
#Number of venues per neighborhood
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Berczy Park                                                            58   
Brockton, Parkdale Village, Exhibition Place                           22   
Business reply mail Processing Centre, South Ce...                     18   
CN Tower, King and Spadina, Railway Lands, Harb...                     14   
Central Bay Street                                                     65   
Christie                                                               17   
Church and Wellesley                                                   76   
Commerce Court, Victoria Hotel                                        100   
Davisville                                                             35   
Davisville North                                                        8   
Dufferin, Dovercourt Village                                           17   
First Canadian Place, Underground city                                100   
Forest Hill North & West, Forest Hill Road Park                         6   
Garden District, Ryerson                                              100   
Harbourfront East, Union Station, Toronto Islands                     100   
High Park, The Junction South                                          25   
India Bazaar, The Beaches West                                         20   
Kensington Market, Chinatown, Grange Park                              63   
Lawrence Park                                                           3   
Little Portugal, Trinity                                               44   
Moore Park, Summerhill East                                             2   
North Toronto West,  Lawrence Park                                     21   
Parkdale, Roncesvalles                                                 15   
Queen's Park, Ontario Provincial Government                            32   
Regent Park, Harbourfront                                              45   
Richmond, Adelaide, King                                               94   
Rosedale                                                                4   
Roselawn                                                                3   
Runnymede, Swansea                                                     34   
St. James Town                                                         79   
St. James Town, Cabbagetown                                            48   
Stn A PO Boxes                                                         97   
Studio District                                                        40   
Summerhill West, Rathnelly, South Hill, Forest ...                     17   
The Annex, North Midtown, Yorkville                                    20   
The Beaches                                                             4   
The Danforth West, Riverdale                                           43   
Toronto Dominion Centre, Design Exchange                              100   
University of Toronto, Harbord                                         34   

                                                    Neighborhood Longitude  \
Neighborhood                                                                 
Berczy Park                                                             58   
Brockton, Parkdale Village, Exhibition Place                            22   
Business reply mail Processing Centre, South Ce...                      18   
CN Tower, King and Spadina, Railway Lands, Harb...                      14   
Central Bay Street                                                      65   
Christie                                                                17   
Church and Wellesley                                                    76   
Commerce Court, Victoria Hotel                                         100   
Davisville                                                              35   
Davisville North                    

In [130]:
#how many unique categories can be curated from all the returned venues
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 236 uniques categories.


In [131]:
#print out the list of categories
toronto_venues['Venue Category'].unique()[:100]

array(['Trail', 'Health Food Store', 'Pub', 'Neighborhood',
       'Cosmetics Shop', 'Greek Restaurant', 'Ice Cream Shop',
       'Italian Restaurant', 'Brewery', 'Fruit & Vegetable Store',
       'Yoga Studio', 'Restaurant', 'Pizza Place', 'Juice Bar',
       'Bookstore', 'Bubble Tea Shop', 'Dessert Shop',
       'Furniture / Home Store', 'Spa', 'Grocery Store', 'Coffee Shop',
       'Bakery', 'Caribbean Restaurant', 'Japanese Restaurant',
       'Indian Restaurant', 'Café', 'Lounge', 'Frozen Yogurt Shop',
       'Liquor Store', 'American Restaurant', 'Gym', 'Fish & Chips Shop',
       'Fast Food Restaurant', 'Sushi Restaurant', 'Park', 'Pet Store',
       'Steakhouse', 'Burrito Place', 'Movie Theater', 'Sandwich Place',
       'Board Shop', 'Fish Market', 'Gay Bar', 'Thai Restaurant',
       'Seafood Restaurant', 'Cheese Shop', 'Comfort Food Restaurant',
       'Middle Eastern Restaurant', 'Stationery Store', 'Coworking Space',
       'Wine Bar', 'Latin American Restaurant', 'Gastrop

In [133]:
# check if the results contain "Italian Restaurants"
"Italian Restaurant" in toronto_venues['Venue Category'].unique()

True

In [134]:
# one hot encoding
to_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
to_onehot['Neighborhoods'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [to_onehot.columns[-1]] + list(to_onehot.columns[:-1])
to_onehot = to_onehot[fixed_columns]

print(to_onehot.shape)
to_onehot.head()

(1623, 237)


Neighborhoods  Afghan Restaurant  Airport  \
0                   The Beaches                  0        0   
1                   The Beaches                  0        0   
2                   The Beaches                  0        0   
3                   The Beaches                  0        0   
4  The Danforth West, Riverdale                  0        0   

   Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0                   0             0               0                0   
1                   0             0               0                0   
2                   0             0               0                0   
3                   0             0               0                0   
4                   0             0               0                0   

   Airport Terminal  American Restaurant  Antique Shop  Aquarium  Art Gallery  \
0                 0                    0             0         0            0   
1                 0                    0             0         0            0   
2                 0                    0             0         0            0   
3                 0                    0             0         0            0   
4                 0                    0             0         0            0   

   Art Museum  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0           0                    0                 0                   0   
1           0                    0                 0                   0   
2           0                    0                 0                   0   
3           0                    0                 0                   0   
4           0                    0                 0                   0   

   Auto Workshop  BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  \
0              0          0           0           0       0     0    0   
1              0          0           0           0       0     0    0   
2              0          0           0           0       0     0    0   
3              0          0           0           0       0     0    0   
4              0          0           0           0       0     0    0   

   Baseball Stadium  Basketball Stadium  Beach  Bed & Breakfast  Beer Bar  \
0                 0                   0      0                0         0   
1                 0                   0      0                0         0   
2                 0                   0      0                0         0   
3                 0                   0      0                0         0   
4                 0                   0      0                0         0   

   Beer Store  Belgian Restaurant  Bistro  Board Shop  Boat or Ferry  \
0           0                   0       0           0              0   
1           0                   0       0           0              0   
2           0                   0       0           0              0   
3           0                   0       0           0              0   
4           0                   0       0           0              0   

   Bookstore  Boutique  Brazilian Restaurant  Breakfast Spot  Brewery  \
0          0         0                     0               0        0   
1          0         0                     0               0        0   
2          0         0                     0               0        0   
3          0         0                     0               0        0   
4          0         0                     0               0        0   

   Bubble Tea Shop  Building  Burger Joint  Burrito Place  Bus Line  Butcher  \
0                0         0             0              0         0        0   
1                0         0             0              0         0        0   
2                0         0             0              0         0        0   
3                0         0             0              0         0        0   
4                0         0             0              0         0        0   

 

In [135]:

to_grouped = to_onehot.groupby(["Neighborhoods"]).mean().reset_index()

print(to_grouped.shape)
to_grouped

(39, 237)


Neighborhoods  Afghan Restaurant  \
0                                         Berczy Park           0.000000   
1        Brockton, Parkdale Village, Exhibition Place           0.000000   
2   Business reply mail Processing Centre, South C...           0.000000   
3   CN Tower, King and Spadina, Railway Lands, Har...           0.000000   
4                                  Central Bay Street           0.000000   
5                                            Christie           0.000000   
6                                Church and Wellesley           0.013158   
7                      Commerce Court, Victoria Hotel           0.000000   
8                                          Davisville           0.000000   
9                                    Davisville North           0.000000   
10                       Dufferin, Dovercourt Village           0.000000   
11             First Canadian Place, Underground city           0.000000   
12    Forest Hill North & West, Forest Hill Road Park           0.000000   
13                           Garden District, Ryerson           0.000000   
14  Harbourfront East, Union Station, Toronto Islands           0.000000   
15                      High Park, The Junction South           0.000000   
16                     India Bazaar, The Beaches West           0.000000   
17          Kensington Market, Chinatown, Grange Park           0.000000   
18                                      Lawrence Park           0.000000   
19                           Little Portugal, Trinity           0.000000   
20                        Moore Park, Summerhill East           0.000000   
21                 North Toronto West,  Lawrence Park           0.000000   
22                             Parkdale, Roncesvalles           0.000000   
23        Queen's Park, Ontario Provincial Government           0.000000   
24                          Regent Park, Harbourfront           0.000000   
25                           Richmond, Adelaide, King           0.000000   
26                                           Rosedale           0.000000   
27                                           Roselawn           0.000000   
28                                 Runnymede, Swansea           0.000000   
29                                     St. James Town           0.000000   
30                        St. James Town, Cabbagetown           0.000000   
31                                     Stn A PO Boxes           0.000000   
32                                    Studio District           0.000000   
33  Summerhill West, Rathnelly, South Hill, Forest...           0.000000   
34                The Annex, North Midtown, Yorkville           0.000000   
35                                        The Beaches           0.000000   
36                       The Danforth West, Riverdale           0.000000   
37           Toronto Dominion Centre, Design Exchange           0.000000   
38                     University of Toronto, Harbord           0.000000   

     Airport  Airport Food Court  Airport Gate  Airport Lounge  \
0   0.000000            0.000000      0.000000        0.000000   
1   0.000000            0.000000      0.000000        0.000000   
2   0.000000            0.000000      0.000000        0.000000   
3   0.071429            0.071429      0.071429        0.142857   
4   0.000000            0.000000      0.000000        0.000000   
5   0.000000            0.000000      0.000000        0.000000   
6   0.000000            0.000000      0.000000        0.000000   
7   0.000000            0.000000      0.000000        0.000000   
8   0.000000            0.000000      0.000000        0.000000   
9   0.000000            0.000000      0.000000        0.000000   
10  0.000000            0.000000      0.000000        0.000000   
11  0.000000            0.000000      0.000000        0.000000   
12  0.000000            0.000000      0.000000        0.000000   
13  0.000000            0.000000      0.000000        0.000000   
14  0.000

In [136]:
len(to_grouped[to_grouped["Italian Restaurant"] > 0])

21

In [137]:
to_Italian = to_grouped[["Neighborhoods","Italian Restaurant"]]
to_Italian

Neighborhoods  Italian Restaurant
0                                         Berczy Park            0.000000
1        Brockton, Parkdale Village, Exhibition Place            0.045455
2   Business reply mail Processing Centre, South C...            0.000000
3   CN Tower, King and Spadina, Railway Lands, Har...            0.000000
4                                  Central Bay Street            0.061538
5                                            Christie            0.058824
6                                Church and Wellesley            0.000000
7                      Commerce Court, Victoria Hotel            0.030000
8                                          Davisville            0.057143
9                                    Davisville North            0.000000
10                       Dufferin, Dovercourt Village            0.000000
11             First Canadian Place, Underground city            0.010000
12    Forest Hill North & West, Forest Hill Road Park            0.000000
13                           Garden District, Ryerson            0.030000
14  Harbourfront East, Union Station, Toronto Islands            0.020000
15                      High Park, The Junction South            0.040000
16                     India Bazaar, The Beaches West            0.050000
17          Kensington Market, Chinatown, Grange Park            0.000000
18                                      Lawrence Park            0.000000
19                           Little Portugal, Trinity            0.022727
20                        Moore Park, Summerhill East            0.000000
21                 North Toronto West,  Lawrence Park            0.000000
22                             Parkdale, Roncesvalles            0.066667
23        Queen's Park, Ontario Provincial Government            0.031250
24                          Regent Park, Harbourfront            0.000000
25                           Richmond, Adelaide, King            0.000000
26                                           Rosedale            0.000000
27                                           Roselawn            0.000000
28                                 Runnymede, Swansea            0.058824
29                                     St. James Town            0.025316
30                        St. James Town, Cabbagetown            0.041667
31                                     Stn A PO Boxes            0.030928
32                                    Studio District            0.025000
33  Summerhill West, Rathnelly, South Hill, Forest...            0.000000
34                The Annex, North Midtown, Yorkville            0.000000
35                                        The Beaches            0.000000
36                       The Danforth West, Riverdale            0.069767
37           Toronto Dominion Centre, Design Exchange            0.030000
38                     University of Toronto, Harbord            0.058824

## Clustering

In [138]:
# set number of clusters
toclusters = 3

to_clustering = to_Italian.drop(["Neighborhoods"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=toclusters, random_state=0).fit(to_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 1, 0, 0, 1, 1, 0, 2, 1, 0], dtype=int32)

In [139]:
# create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.
to_merged = to_Italian.copy()

# add clustering labels
to_merged["Cluster Labels"] = kmeans.labels_

In [140]:
to_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
to_merged.head()

Neighborhood  Italian Restaurant  \
0                                        Berczy Park            0.000000   
1       Brockton, Parkdale Village, Exhibition Place            0.045455   
2  Business reply mail Processing Centre, South C...            0.000000   
3  CN Tower, King and Spadina, Railway Lands, Har...            0.000000   
4                                 Central Bay Street            0.061538   

   Cluster Labels  
0               0  
1               1  
2               0  
3               0  
4               1

In [141]:
# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
to_merged = to_merged.join(toronto_venues.set_index("Neighborhood"), on="Neighborhood")

print(to_merged.shape)
to_merged.head()

(1623, 9)


Neighborhood  Italian Restaurant  Cluster Labels  Neighborhood Latitude  \
0  Berczy Park                 0.0               0              43.644771   
0  Berczy Park                 0.0               0              43.644771   
0  Berczy Park                 0.0               0              43.644771   
0  Berczy Park                 0.0               0              43.644771   
0  Berczy Park                 0.0               0              43.644771   

   Neighborhood Longitude                                      Venue  \
0              -79.373306                                       LCBO   
0              -79.373306       The Keg Steakhouse + Bar - Esplanade   
0              -79.373306                              Meridian Hall   
0              -79.373306                             Fresh On Front   
0              -79.373306  Hockey Hall Of Fame (Hockey Hall of Fame)   

   Venue Latitude  Venue Longitude                 Venue Category  
0       43.642944       -79.372440                   Liquor Store  
0       43.646712       -79.374768                     Restaurant  
0       43.646292       -79.376022                   Concert Hall  
0       43.647815       -79.374453  Vegetarian / Vegan Restaurant  
0       43.646974       -79.377323                         Museum

In [143]:
# sort the results by Cluster Labels
print(to_merged.shape)
to_merged.sort_values(["Cluster Labels"], inplace=True)
to_merged

(1623, 9)


Neighborhood  Italian Restaurant  \
0                                         Berczy Park            0.000000   
24                          Regent Park, Harbourfront            0.000000   
25                           Richmond, Adelaide, King            0.000000   
25                           Richmond, Adelaide, King            0.000000   
25                           Richmond, Adelaide, King            0.000000   
24                          Regent Park, Harbourfront            0.000000   
24                          Regent Park, Harbourfront            0.000000   
24                          Regent Park, Harbourfront            0.000000   
24                          Regent Park, Harbourfront            0.000000   
24                          Regent Park, Harbourfront            0.000000   
24                          Regent Park, Harbourfront            0.000000   
24                          Regent Park, Harbourfront            0.000000   
25                           Richmond, Adelaide, King            0.000000   
25                           Richmond, Adelaide, King            0.000000   
25                           Richmond, Adelaide, King            0.000000   
25                           Richmond, Adelaide, King            0.000000   
25                           Richmond, Adelaide, King            0.000000   
25                           Richmond, Adelaide, King            0.000000   
25                           Richmond, Adelaide, King            0.000000   
25                           Richmond, Adelaide, King            0.000000   
25                           Richmond, Adelaide, King            0.000000   
25                           Richmond, Adelaide, King            0.000000   
25                           Richmond, Adelaide, King            0.000000   
25                           Richmond, Adelaide, King            0.000000   
25                           Richmond, Adelaide, King            0.000000   
25                           Richmond, Adelaide, King            0.000000   
25                           Richmond, Adelaide, King            0.000000   
25                           Richmond, Adelaide, King            0.000000   
25                           Richmond, Adelaide, King            0.000000   
25                           Richmond, Adelaide, King            0.000000   
25                           Richmond, Adelaide, King            0.000000   
25                           Richmond, Adelaide, King            0.000000   
25                           Richmond, Adelaide, King            0.000000   
25                           Richmond, Adelaide, King            0.000000   
25                           Richmond, Adelaide, King            0.000000   
25                           Richmond, Adelaide, King            0.000000   
3   CN Tower, King and Spadina, Railway Lands, Har...            0.000000   
3   CN Tower, King and Spadina, Railway Lands, Har...            0.000000   
3   CN Tower, King and Spadina, Railway Lands, Har...            0.000000   
3   CN Tower, King and Spadina, Railway Lands, Har...            0.000000   
3   CN Tower, King and Spadina, Railway Lands, Har...            0.000000   
3   CN Tower, King and Spadina, Railway Lands, Har...            0.000000   
3   CN Tower, King and Spadina, Railway Lands, Har...            0.000000   
3   CN Tower, King and Spadina, Railway Lands, Har...            0.000000   
9                                    Davisville North            0.000000   
6                                Church and Wellesley            0.000000   
6                                Church and Wellesley            0.000000   
6                                Church and Wellesley            0.000000   
6                                Church and Wellesley            0.000000   
6                                Church and Wellesley            0.000000   
3   CN Tower, King and Spadina, Railway Lands, Har...            0.000000   
25                           Richmond

## Visualize the Clusters

In [144]:
# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

In [148]:
#visualize the resulting clusters

map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(toclusters)
ys = [i+x+(i*x)**2 for i in range(toclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(to_merged['Neighborhood Latitude'], to_merged['Neighborhood Longitude'], to_merged['Neighborhood'], to_merged['Cluster Labels']):
    label = folium.Popup('{} ({}): {} - Cluster {}'.format(lat, lon, poi, cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [147]:
# save the map as HTML file
map_clusters.save('map_clusters.html')

In [149]:

#Cluster 0
to_merged.loc[to_merged['Cluster Labels'] == 0]

Neighborhood  Italian Restaurant  \
0                                         Berczy Park                0.00   
24                          Regent Park, Harbourfront                0.00   
25                           Richmond, Adelaide, King                0.00   
25                           Richmond, Adelaide, King                0.00   
25                           Richmond, Adelaide, King                0.00   
24                          Regent Park, Harbourfront                0.00   
24                          Regent Park, Harbourfront                0.00   
24                          Regent Park, Harbourfront                0.00   
24                          Regent Park, Harbourfront                0.00   
24                          Regent Park, Harbourfront                0.00   
24                          Regent Park, Harbourfront                0.00   
24                          Regent Park, Harbourfront                0.00   
25                           Richmond, Adelaide, King                0.00   
25                           Richmond, Adelaide, King                0.00   
25                           Richmond, Adelaide, King                0.00   
25                           Richmond, Adelaide, King                0.00   
25                           Richmond, Adelaide, King                0.00   
25                           Richmond, Adelaide, King                0.00   
25                           Richmond, Adelaide, King                0.00   
25                           Richmond, Adelaide, King                0.00   
25                           Richmond, Adelaide, King                0.00   
25                           Richmond, Adelaide, King                0.00   
25                           Richmond, Adelaide, King                0.00   
25                           Richmond, Adelaide, King                0.00   
25                           Richmond, Adelaide, King                0.00   
25                           Richmond, Adelaide, King                0.00   
25                           Richmond, Adelaide, King                0.00   
25                           Richmond, Adelaide, King                0.00   
25                           Richmond, Adelaide, King                0.00   
25                           Richmond, Adelaide, King                0.00   
25                           Richmond, Adelaide, King                0.00   
25                           Richmond, Adelaide, King                0.00   
25                           Richmond, Adelaide, King                0.00   
25                           Richmond, Adelaide, King                0.00   
25                           Richmond, Adelaide, King                0.00   
25                           Richmond, Adelaide, King                0.00   
3   CN Tower, King and Spadina, Railway Lands, Har...                0.00   
3   CN Tower, King and Spadina, Railway Lands, Har...                0.00   
3   CN Tower, King and Spadina, Railway Lands, Har...                0.00   
3   CN Tower, King and Spadina, Railway Lands, Har...                0.00   
3   CN Tower, King and Spadina, Railway Lands, Har...                0.00   
3   CN Tower, King and Spadina, Railway Lands, Har...                0.00   
3   CN Tower, King and Spadina, Railway Lands, Har...                0.00   
3   CN Tower, King and Spadina, Railway Lands, Har...                0.00   
9                                    Davisville North                0.00   
6                                Church and Wellesley                0.00   
6                                Church and Wellesley                0.00   
6                                Church and Wellesley                0.00   
6                                Church and Wellesley                0.00   
6                                Church and Wellesley                0.00   
3   CN Tower, King and Spadina, Railway Lands, Har...                0.00   
25                           Richmond

In [150]:
#Cluster 1
to_merged.loc[to_merged['Cluster Labels'] == 1]

Neighborhood  Italian Restaurant  \
4                             Central Bay Street            0.061538   
4                             Central Bay Street            0.061538   
4                             Central Bay Street            0.061538   
4                             Central Bay Street            0.061538   
4                             Central Bay Street            0.061538   
4                             Central Bay Street            0.061538   
4                             Central Bay Street            0.061538   
4                             Central Bay Street            0.061538   
4                             Central Bay Street            0.061538   
4                             Central Bay Street            0.061538   
4                             Central Bay Street            0.061538   
28                            Runnymede, Swansea            0.058824   
4                             Central Bay Street            0.061538   
4                             Central Bay Street            0.061538   
4                             Central Bay Street            0.061538   
4                             Central Bay Street            0.061538   
4                             Central Bay Street            0.061538   
4                             Central Bay Street            0.061538   
4                             Central Bay Street            0.061538   
4                             Central Bay Street            0.061538   
4                             Central Bay Street            0.061538   
4                             Central Bay Street            0.061538   
4                             Central Bay Street            0.061538   
4                             Central Bay Street            0.061538   
4                             Central Bay Street            0.061538   
4                             Central Bay Street            0.061538   
4                             Central Bay Street            0.061538   
4                             Central Bay Street            0.061538   
4                             Central Bay Street            0.061538   
4                             Central Bay Street            0.061538   
4                             Central Bay Street            0.061538   
4                             Central Bay Street            0.061538   
4                             Central Bay Street            0.061538   
28                            Runnymede, Swansea            0.058824   
4                             Central Bay Street            0.061538   
28                            Runnymede, Swansea            0.058824   
28                            Runnymede, Swansea            0.058824   
28                            Runnymede, Swansea            0.058824   
28                            Runnymede, Swansea            0.058824   
28                            Runnymede, Swansea            0.058824   
28                            Runnymede, Swansea            0.058824   
28                            Runnymede, Swansea            0.058824   
28                            Runnymede, Swansea            0.058824   
28                            Runnymede, Swansea            0.058824   
28                            Runnymede, Swansea            0.058824   
28                            Runnymede, Swansea            0.058824   
28                            Runnymede, Swansea            0.058824   
28                            Runnymede, Swansea            0.058824   
4                             Central Bay Street            0.061538   
28                            Runnymede, Swansea            0.058824   
28                            Runnymede, Swansea            0.058824   
28                            Runnymede, Swansea            0.058824   
28                            Runnymede, Swansea            0.058824   
4                             Central Bay Street            0.061538   
4                             Central Bay Street            0.061538   
4   

In [151]:
#Cluster 2
to_merged.loc[to_merged['Cluster Labels'] == 2]

Neighborhood  Italian Restaurant  \
15                      High Park, The Junction South            0.040000   
15                      High Park, The Junction South            0.040000   
15                      High Park, The Junction South            0.040000   
15                      High Park, The Junction South            0.040000   
15                      High Park, The Junction South            0.040000   
15                      High Park, The Junction South            0.040000   
15                      High Park, The Junction South            0.040000   
15                      High Park, The Junction South            0.040000   
14  Harbourfront East, Union Station, Toronto Islands            0.020000   
14  Harbourfront East, Union Station, Toronto Islands            0.020000   
19                           Little Portugal, Trinity            0.022727   
19                           Little Portugal, Trinity            0.022727   
14  Harbourfront East, Union Station, Toronto Islands            0.020000   
14  Harbourfront East, Union Station, Toronto Islands            0.020000   
14  Harbourfront East, Union Station, Toronto Islands            0.020000   
14  Harbourfront East, Union Station, Toronto Islands            0.020000   
15                      High Park, The Junction South            0.040000   
14  Harbourfront East, Union Station, Toronto Islands            0.020000   
14  Harbourfront East, Union Station, Toronto Islands            0.020000   
15                      High Park, The Junction South            0.040000   
15                      High Park, The Junction South            0.040000   
19                           Little Portugal, Trinity            0.022727   
15                      High Park, The Junction South            0.040000   
19                           Little Portugal, Trinity            0.022727   
19                           Little Portugal, Trinity            0.022727   
14  Harbourfront East, Union Station, Toronto Islands            0.020000   
19                           Little Portugal, Trinity            0.022727   
19                           Little Portugal, Trinity            0.022727   
19                           Little Portugal, Trinity            0.022727   
19                           Little Portugal, Trinity            0.022727   
19                           Little Portugal, Trinity            0.022727   
19                           Little Portugal, Trinity            0.022727   
15                      High Park, The Junction South            0.040000   
19                           Little Portugal, Trinity            0.022727   
7                      Commerce Court, Victoria Hotel            0.030000   
7                      Commerce Court, Victoria Hotel            0.030000   
7                      Commerce Court, Victoria Hotel            0.030000   
7                      Commerce Court, Victoria Hotel            0.030000   
15                      High Park, The Junction South            0.040000   
15                      High Park, The Junction South            0.040000   
15                      High Park, The Junction South            0.040000   
15                      High Park, The Junction South            0.040000   
15                      High Park, The Junction South            0.040000   
15                      High Park, The Junction South            0.040000   
14  Harbourfront East, Union Station, Toronto Islands            0.020000   
15                      High Park, The Junction South            0.040000   
14  Harbourfront East, Union Station, Toronto Islands            0.020000   
19                           Little Portugal, Trinity            0.022727   
19                           Little Portugal, Trinity            0.022727   
19                           Little Portugal, Trinity            0.022727   
19                           Little Portugal, Trinity            0.022727   
19                           Little P

## Conclusion

Most of Italian restaurants are in Cluster 1. In Cluster 1, Italian restaurants are most likely to locate around Central Bay Street, Runnymede Swansea and the Beaches Street where many restaurants shops around. There are some Italian restaurants in Cluster 2 which is also business areas especially restaurant area. Looking at nearby venues, it seems Cluster 1 might be a better location comparing to Cluster 2 as there are a lot of restaurants in these areas. Therefore, the entrepreneur should open the Italian restaurant in Cluster 1 areas. However, one thing that the entrepreneur should consider is the competition. The entrepreneur would better to seek more information about the market competition to decide the location and maximize the profits.